In [0]:
%pip install google-generativeai

Note: you may need to restart the kernel using %restart_python or dbutils.library.restartPython() to use updated packages.


In [0]:
%restart_python

In [0]:
from pyspark.sql.types import *
import pyspark
from pyspark.sql import SparkSession
from pyspark.sql.functions import col, udf, regexp_extract, explode, lower, length, trim, when, regexp_replace, collect_list, struct, concat_ws
from pyspark.sql import functions as F
import sparknlp
from pyspark.ml.feature import VectorAssembler
from pyspark.ml.linalg import Vectors
from pyspark.ml.functions import array_to_vector
import pandas as pd
import numpy as np
import re
import matplotlib.pyplot as plt

In [0]:
spark = sparknlp.start()
clusters_pd = pd.read_csv('data/clustering_4options.csv')
requirements_clusters = spark.createDataFrame(clusters_pd)
cluster_titles_pd = pd.read_csv('data/Grouped_Clusters.csv')
final_clusters = spark.createDataFrame(cluster_titles_pd)

In [0]:
def to_float_array(embedding_str):
    return [float(x) for x in embedding_str.strip("[]").split(",")]
def to_int_array(embedding_str):
    return [int(x) for x in embedding_str.strip("[]").split(",")]
def to_string_array(embedding_str):
    return [x for x in embedding_str.strip("[]").split(",")]
    
to_float_array_udf = udf(to_float_array, ArrayType(FloatType()))
requirements_clusters = requirements_clusters.withColumn("Embeddings", to_float_array_udf(col("Embeddings_Model1"))).drop("Embeddings_Model1", "Embeddings_Model2")
to_int_array_udf = udf(to_int_array, ArrayType(IntegerType()))
to_string_array_udf = udf(to_string_array, ArrayType(StringType()))
final_clusters = final_clusters.withColumn("Clusters", to_int_array_udf(col("Clusters"))).withColumn("Job_Titles", to_string_array_udf(col("Job_Titles")))


# Map cluster numbers to cluster titles
cluster_mapping = final_clusters.select(explode("Clusters").alias("Cluster"), "Cluster_Title")
requirements_clusters_new = requirements_clusters.join(
    cluster_mapping,
    requirements_clusters["Cluster_spark_KMeans_1"] == cluster_mapping["Cluster"],      # TODO: chose model
    how="left"
).drop("Cluster")
requirements_clusters_new.display()

Title Company Full Job Description Search Word Description Description_English Requirements_Text Cluster_spark_KMeans_1 Cluster_spark_KMeans_2 Cluster_DBSCAN_Model1 Cluster_DBSCAN_Model2 Embeddings Cluster_Title Data Analytics Apple Summary Posted: Nov 7, 2024 Role Number: 200577967 We're looking for an exceptional data analyst with a strong background in distributed data processing and a demonstrated ability to turn data into actionable insights. As a data analyst for our Storage Data Analytics team at Apple, you'll play a crucial role in developing the fastest and most efficient SSDs for our products, including the iPhone, iPad, Apple Watch, and new Apple Silicon Macs. If you're passionate about continuously improving the ways we use data to make Apple's products amazing, we want to hear from you! Description On the Storage Data Analytics team, we are responsible for performing ad hoc data analysis, development and maintenance of distributed data pipelines, as well as creation and support of analysis tools. Our team focuses on Apple’s storage solutions. It is small and nimble, able to quickly explore ideas and present them to the storage teams and to leadership. Minimum Qualifications +3 years of experience Ability to lead data investigations and analysis projects with ambiguous requirements Advanced statistic and modeling knowledge Experience visualizing and presenting analyses in tools like Jupyter and Tableau Experience programming in Python in a professional setting Familiarity with distributed computation, storage, and workflow management (e.g. Splunk, Spark, Kubernetes, Kafka, Hadoop, MapReduce, AirFlow etc.) Experience with relational databases and SQL Highly organized, creative, motivated, and passionate about achieving results Curious and have excellent analytical and problem solving skills Excellent written, verbal, and data communication skills Bachelor's or Master's degree in computer science. Preferred Qualifications Familiarity with distributed computation, storage, and workflow management (e.g. Splunk, Spark, Kubernetes, Kafka, Hadoop, MapReduce, AirFlow etc.) Opened URL: https://il.indeed.com/rc/clk?jk=0433bc7e45e694a3&bb=r6UIYw2mow7Pn8IzQwq2_7gXyX4L0a9oUPOLDIseoxAN8l0MRFFfCqpU6vSJRCmVlzxZCXcY6V-lzbB66NkEzDukGjQJgUJrBPff0HR1apFcJos6F0MbonwvLMjHhNz9&xkcb=SoDD67M33wH7H8WWaB0JbzkdCdPP&fccid=8e007f7a76f9cee5&vjs=3 data Summary Posted: Nov 7, 2024 Role Number: 200577967 We're looking for an exceptional data analyst with a strong background in distributed data processing and a demonstrated ability to turn data into actionable insights. As a data analyst for our Storage Data Analytics team at Apple, you'll play a crucial role in developing the fastest and most efficient SSDs for our products, including the iPhone, iPad, Apple Watch, and new Apple Silicon Macs. If you're passionate about continuously improving the ways we use data to make Apple's products amazing, we want to hear from you! Description On the Storage Data Analytics team, we are responsible for performing ad hoc data analysis, development and maintenance of distributed data pipelines, as well as creation and support of analysis tools. Our team focuses on Apple’s storage solutions. It is small and nimble, able to quickly explore ideas and present them to the storage teams and to leadership. Minimum Qualifications +3 years of experience Ability to lead data investigations and analysis projects with ambiguous requirements Advanced statistic and modeling knowledge Experience visualizing and presenting analyses in tools like Jupyter and Tableau Experience programming in Python in a professional setting Familiarity with distributed computation, storage, and workflow management (e.g. Splunk, Spark, Kubernetes, Kafka, Hadoop, MapReduce, AirFlow etc.) Experience with relational databases and SQL Highly organized, creative, motivated, and passionate about achieving results Curious and have excellent analytical and problem solving skills Excellent written, verbal

In [0]:
requirements_clusters_new.count()

647

In [0]:
import pandas as pd

#requ = pd.read_csv('/Workspace/Users/tamar.dufour@campus.technion.ac.il/data/indeed_clusters_titles_28_01.csv')
#requ = requ[["Title", "Company", "Requirements_Text", "Cluster_Title"]]
#spark_requ = spark.createDataFrame(requ)
spark_requ = requirements_clusters_new.select("Title", "Company", "Requirements_Text", "Cluster_Title")
spark_requ.display()

Title Company Requirements_Text Cluster_Title Data Analytics Apple +3 years of experience Ability to lead data investigations and analysis projects with ambiguous requirements Advanced statistic and modeling knowledge Experience visualizing and presenting analyses in tools like Jupyter and Tableau Experience programming in Python in a professional setting Familiarity with distributed computation, storage, and workflow management (e.g. Splunk, Spark, Kubernetes, Kafka, Hadoop, MapReduce, AirFlow etc.) Experience with relational databases and SQL Highly organized, creative, motivated, and passionate about achieving results Curious and have excellent analytical and problem solving skills Excellent written, verbal, and data communication skills Bachelor's or Master's degree in computer science. Preferred Qualifications Familiarity with distributed computation, storage, and workflow management (e.g. Splunk, Spark, Kubernetes, Kafka, Hadoop, MapReduce, AirFlow etc.) data Junior Backend Big Data Developer ThetaRay into actionable designs and tasks, development, UT, and production troubleshooting Requirements 1-2 years of experience of hands-on development experience Experience developing data-oriented products preferably using Python/Java Experience in data processing FW such as Spark, Pandas, Hadoop, Airflow Experience in Distributed Databases (Such as Elasticsearch, Mongo, Redis, etc) Experience with developing microservices-based architecture Experience working in container-based environments using tools such as K8s, helm Experience working as a software developer in an Agile environment Nice to have: Experience in machine learning FWs such as SKLearn, Tensorflow Experience with RedHat OpenShift Dev Environment knowledge: GIT, Jenkins, Docker junior backend Data Annotator Prisma Photonics A Bachelor of Science degree or equivalent (STEM fields an advantage). Strong attention to detail and a commitment to maintaining high-quality annotation standards. Good written and verbal skills, with the ability to work effectively with a diverse group of individuals. Availability to work full time when needed. Nice-to-haves: Familiarity with data annotation processes, especially non-structured data (images, video, audio). Experience working with seismic data, heat maps, or spectrograms Familiarity with SQL and data visualization tools. Experience with coding languages, preferably MATLAB and Python. data scientist Marketing Data Analyst Plarium B.A/BSc in a highly quantitative field such as mathematics industrial engineering economics statistics or equivalent academic knowledge At least 2 years of hands-on data analysis and story-telling experience Proven experience with measuring online success and identifying optimization opportunities Excellent understanding of online marketing metrics High proficiency in SQL with demonstrated experience in querying large complex datasets Strong Excel / Google Sheets skills Experience with data visualization tools such as Qlik Sense and Looker A solid grasp of statistical significance models and tools Desired Marketing metrics of user funnel, user acquisition KPI’s What we offer A Workplace Designed for Your Well-Being - Comfortable Environment: Ergonomic chairs and desks to support your health. Beautifully designed spaces that inspire creativity. - On-Site Amenities: Gym, yoga room, and music room for relaxation and rejuvenation. - Delicious Perks: 5-star breakfast to kickstart your day. Freshly made coffee, shakes, and afternoon salads by our in-house barista. - Health & Wellness: Full health insurance coverage for your peace of mind. - Growth Opportunities: Learning and training programs to enhance your personal and professional skills. - Vibrant Culture: Happy hours, team events, and plenty of opportunities to connect with colleagues. Join us and experience a workplace where your well-being, growth, and enjoyment come first! data Junior Data Analyst aiOla B.Sc in Industrial Engineering, Data Analytics, S

In [0]:
spark_requ.count()

647

In [0]:
num_records = spark_requ.count()
batch_size = num_records/2

In [0]:
spark_requ.columns

['Title', 'Company', 'Requirements_Text', 'Cluster_Title']

In [0]:
import google.generativeai as genai
import json

#spark_requ = spark_requ.select('Title', 'Company', 'Requirements_Text')
#requ = requ[['Title', 'Company', 'Requirements_Text']]

api_key = 'USE YOUR API KEY'
genai.configure(api_key=api_key)
model = genai.GenerativeModel("gemini-1.5-flash")

response_dict = {}
#for i in range(0, int(num_records), int(batch_size)):
cluster_titles = spark_requ.select("Cluster_Title").distinct().collect()
cluster_titles = [row["Cluster_Title"] for row in cluster_titles]
# Iterate over the distinct clusters
for title in cluster_titles:
    print("Cluster: ", str(title))
    mini_requ = spark_requ.filter(col("Cluster_Title") == title)
    mini_requ = mini_requ.select("Title", "Company", "Requirements_Text")
    #start = i
    #end = min(int(i + batch_size), int(num_records))
    #mini_requ = requ[start:end]

    # Convert to JSON string
    df_as_text = mini_requ.toPandas().to_json(orient="records")

    # Append the JSON string to the prompt
    prompt = f"""
    This is a df: {df_as_text}.
    I want to extract the tools and requirements from the Requirements_Text column. 
    The result for each row should be in this format: [Title- Company- Requirement1, Requirement2, Requirement3...]. 
    Example requirements: Python, SQL, 3 years of experience, communication skills, etc.
    Split values containing multiple items separated by "/", such as "Python/C++/C#/Scala", into individual requirements: "Python", "C++", "C#", and "Scala". 
    Do not write any other explanations; return the results in the given format. Ensure extracted experience is in as few words as possible.
    """
    response = model.generate_content(prompt)

    response_dict[title] = response.text

Cluster:  data scientist
Cluster:  junior backend
Cluster:  data
Cluster:  manager junior
Cluster:  manager
Cluster:  customer manager
Cluster:  data entry
Cluster:  software
Cluster:  data analyst
Cluster:  frontend developer
Cluster:  developer software
Cluster:  entry engineer
Cluster:  freelance reader:
Cluster:  developer frontend


In [0]:
from pyspark.sql import SparkSession
from pyspark.sql.types import StructType, StructField, StringType
import re
from pyspark.sql.functions import lit, split

all_dfs_results = {}

# Define a function to parse a single line
def parse_line(line):
    content = line.strip("[]")  # Remove square brackets
    parts = re.split(r"-", content, maxsplit=2)  # Split by "-" with max 2 splits
    print("parts: ", parts)
    print(len(parts))
    if len(parts) == 3:
        title, company, requirements = parts
        return title.strip(), company.strip(), requirements.strip()
    return None, None, None

for title, text_res in response_dict.items():

    # Initialize Spark session
    spark = SparkSession.builder.appName("ParseText").getOrCreate()

    lines = [line.strip() for line in text_res.split("\n") if line.strip()]

    # Parse lines and create an RDD
    parsed_data = [parse_line(line) for line in lines]

    # Define schema for the DataFrame
    schema = StructType([
        StructField("Title", StringType(), True),
        StructField("Company", StringType(), True),
        StructField("Requirements", StringType(), True)
    ])

    # Create a Spark DataFrame
    df = spark.createDataFrame(parsed_data, schema=schema)
    #df.display()

    all_dfs_results[title] = df

    num_positions = df.dropna(subset=["Requirements"]).count()
    # Step 1: Convert the "Requirements" column to lowercase
    df = df.withColumn("Requirements", lower(col("Requirements")))
    df = df.withColumn("Requirements", regexp_replace(col("Requirements"), r"\+| and |[\[\]]", ""))

    # Step 2: Split the "Requirements" column into individual requirements
    df = df.withColumn("Requirement", explode(split(col("Requirements"), ",")))

    # Step 3: Trim whitespace from each requirement
    df = df.withColumn("Requirement", trim(col("Requirement")))

    # Step 4: Group by "Requirement" and count occurrences
    requirement_counts = df.groupBy("Requirement").count()

    # Step 5: Order by count in descending order
    requirement_counts = requirement_counts.orderBy(col("count").desc())

    requirement_counts = requirement_counts.withColumn("% adds", (col("count") / num_positions) * 100)

    # Show the result
    requirement_counts = requirement_counts.withColumn("Cluster_title", lit(title))
    all_dfs_results[title] = requirement_counts
    requirement_counts.display()

parts:  ['```json']
1
parts:  ['']
1
parts:  ['"Data Annotator', ' Prisma Photonics', ' Bachelor\'s degree, Strong attention to detail, Good written and verbal skills, Full-time availability, Familiarity with data annotation processes, Experience with seismic data, Familiarity with SQL, Experience with MATLAB, Experience with Python",']
3
parts:  ['"Data Engineer', ' Meta', ' Bachelor\'s degree, 4+ years experience, SQL, ETL, Data modeling, Python",']
3
parts:  ['"data scientist!', ' Horizon Technologies', ' 3+ years data experience, 1+ year data science experience, Tabular mining tools experience, Healthcare mining experience, Free text mining",']
3
parts:  ['"Data Scientist', ' Ticomsoft', ' Bachelor\'s degree, Strong algorithm development skills, Machine learning algorithms experience, Optimization algorithms experience, 5+ years Python/R/Matlab experience, Strong communication skills, Big data experience",']
3
parts:  ['"data scientist', ' OSR Enterprises', ' 4+ years experience, S

Requirement count % adds Cluster_title 154 99.35483870967742 data scientist python 87 56.12903225806451 data scientist sql 42 27.09677419354839 data scientist 4 years experience 29 18.70967741935484 data scientist bachelor's degree 25 16.129032258064516 data scientist pytorch 23 14.838709677419354 data scientist machine learning algorithms experience 19 12.258064516129032 data scientist 5 years python/r/matlab experience 19 12.258064516129032 data scientist machine learning techniques 19 12.258064516129032 data scientist strong algorithm development skills 19 12.258064516129032 data scientist tabular mining tools experience 19 12.258064516129032 data scientist optimization algorithms experience 19 12.258064516129032 data scientist javascript 19 12.258064516129032 data scientist big data experience" 19 12.258064516129032 data scientist free text mining" 19 12.258064516129032 data scientist 1 year data science experience 19 12.258064516129032 data scientist strong communication skills 19 12.258064516129032 data scientist mongodb" 19 12.258064516129032 data scientist strong problem-solving skills 19 12.258064516129032 data scientist healthcare mining experience 19 12.258064516129032 data scientist stock/futures prediction experience 19 12.258064516129032 data scientist tensorflow 19 12.258064516129032 data scientist 3 years data experience 18 11.612903225806452 data scientist data visualization 18 11.612903225806452 data scientist machine learning 17 10.967741935483872 data scientist 3 years experience 17 10.967741935483872 data scientist numpy 15 9.67741935483871 data scientist r 15 9.67741935483871 data scientist data mining 12 7.741935483870968 data scientist data modeling 11 7.096774193548387 data scientist etl 11 7.096774193548387 data scientist python" 11 7.096774193548387 data scientist data cleaning 11 7.096774193548387 data scientist ai algorithms 11 7.096774193548387 data scientist statistical analysis 11 7.096774193548387 data scientist gcp" 11 7.096774193548387 data scientist statistical modeling 11 7.096774193548387 data scientist devops 10 6.451612903225806 data scientist msc 10 6.451612903225806 data scientist machine learning algorithms 10 6.451612903225806 data scientist tableau/power bi/plotly 10 6.451612903225806 data scientist statistical methods 10 6.451612903225806 data scientist opencv 10 6.451612903225806 data scientist nosql databases 10 6.451612903225806 data scientist deep learning frameworks 10 6.451612903225806 data scientist mlops" 10 6.451612903225806 data scientist 5-7 years experience 10 6.451612903225806 data scientist big data tools 10 6.451612903225806 data scientist nlp/computer vision/time-series forecasting 10 6.451612903225806 data scientist scikit-learn 9 5.806451612903226 data scientist pandas 9 5.806451612903226 data scientist cloud infrastructure 9 5.806451612903226 data scientist llms 9 5.806451612903226 data scientist identity management" 9 5.806451612903226 data scientist computer vision algorithms 9 5.806451612903226 data scientist vector dbs 9 5.806451612903226 data scientist good writtenverbal skills 8 5.161290322580645 data scientist familiarity with data annotation processes 8 5.161290322580645 data scientist full-time availability 8 5.161290322580645 data scientist experience with python" 8 5.161290322580645 data scientist experience with seismic data 8 5.161290322580645 data scientist familiarity with sql 8 5.161290322580645 data scientist strong attention to detail 8 5.161290322580645 data scientist experience with matlab 8 5.161290322580645 data scientist dbt 8 5.161290322580645 data scientist bigquery 8 5.161290322580645 data scientist audio analysis 8 5.161290322580645 data scientist master's/phd 8 5.161290322580645 data scientist 6 years experience 8 5.161290322580645 data scientist nlp 8 5.161290322580645 data scientist tableau" 8 5.161290322580645 data scientist looker 8 5.161290322580645 data scientist bachelor of science degree 7 4.516129032258064 data scientist git" 

parts:  ['```']
1
parts:  ["'Junior Backend Big Data Developer", ' ThetaRay', " 1-2 years experience, Python, Java, Spark, Pandas, Hadoop, Airflow, Elasticsearch, Mongo, Redis, microservices, K8s, helm, Agile, GIT, Jenkins, Docker', 'Junior Backend Big Data Developer- , developing the next-generation smart-infrastructure solution based on novel fiber-sensing technology (smart roads, smart cities, perimeters, grid monitoring, etc.). The company offers an award-winning disruptive solution – a “sensor free” approach to smart infrastructure. The company is VC backed and is in the revenues stage.- 1-2 years experience, Python, Java, Spark, Pandas, Hadoop, Airflow, Elasticsearch, Mongo, Redis, microservices, K8s, helm, Agile, GIT, Jenkins, Docker', 'Junior Backend Big Data Developer- Twingo- 1-2 years experience, Python, Java, Spark, Pandas, Hadoop, Airflow, Elasticsearch, Mongo, Redis, microservices, K8s, helm, Agile, GIT, Jenkins, Docker', 'Junior Backend Big Data Developer- culture where 

Requirement count % adds Cluster_title airflow 8 800.0 junior backend helm 8 800.0 junior backend docker' 8 800.0 junior backend pandas 8 800.0 junior backend jenkins 8 800.0 junior backend agile 8 800.0 junior backend spark 8 800.0 junior backend mongo 8 800.0 junior backend elasticsearch 8 800.0 junior backend redis 8 800.0 junior backend k8s 8 800.0 junior backend java 8 800.0 junior backend git 8 800.0 junior backend microservices 8 800.0 junior backend hadoop 8 800.0 junior backend python 8 800.0 junior backend smart cities 2 200.0 junior backend etc.). the company offers an award-winning disruptive solution – a “sensor free” approach to smart infrastructure. the company is vc backedis in the revenues stage.- 1-2 years experience 2 200.0 junior backend grid monitoring 2 200.0 junior backend perimeters 2 200.0 junior backend developing the next-generation smart-infrastructure solution based on novel fiber-sensing technology (smart roads 2 200.0 junior backend hiring 1 100.0 junior backend placement 1 100.0 junior backend leaves of absence 1 100.0 junior backend promotion 1 100.0 junior backend compensationtraining.- 1-2 years experience 1 100.0 junior backend 'junior backend big data developer- twingo- 1-2 years experience 1 100.0 junior backend including recruiting 1 100.0 junior backend layoff 1 100.0 junior backend 'junior backend big data developer- culture where all employees feel they can bring their authentic selves to workbe successful.- 1-2 years experience 1 100.0 junior backend 1-2 years experience 1 100.0 junior backend recall 1 100.0 junior backend 'null- brandshield- 1-2 years experience 1 100.0 junior backend 'junior backend big data developer- 1 100.0 junior backend 'null- 1 100.0 junior backend 'null- build a diverse company that provides equitable access to growthsuccess for all employees globally.- 1-2 years experience 1 100.0 junior backend termination 1 100.0 junior backend 'null- has facilities. this policy applies to all termsconditions of employment 1 100.0 junior backend transfer 1 100.0 junior backend

parts:  ['```json']
1
parts:  ['']
1
parts:  ['"Data Analytics', ' Apple', ' 3 years experience, Lead data investigations, Advanced statistics, Modeling knowledge, Visualizing analyses, Jupyter, Tableau, Python programming, Distributed computation, Splunk, Spark, Kubernetes, Kafka, Hadoop, MapReduce, AirFlow, Relational databases, SQL, Organized, Creative, Motivated, Analytical skills, Problem-solving skills, Written communication, Verbal communication, Data communication, Bachelor\'s degree",']
3
parts:  ['"Marketing Data Analyst', ' Plarium', ' B.A./B.Sc, Mathematics, Industrial engineering, Economics, Statistics, 2 years experience, Data analysis, Storytelling, Measuring online success, Optimization opportunities, Online marketing metrics, SQL, Excel, Google Sheets, Qlik Sense, Looker, Statistical models",']
3
parts:  ['"Junior Data Analyst', ' aiOla', ' B.Sc, Industrial Engineering, Data Analytics, Statistics, Python, Pandas, SQL, Tableau, Communication skills, English fluency, 0-1

...

Requirement count % adds Cluster_title 11 91.66666666666666 entry engineer work location: remote" 8 66.66666666666666 entry engineer working in the labor movement 3 25.0 entry engineer some limited travel" 3 25.0 entry engineer long/irregular hours 3 25.0 entry engineer sitting at a computer workstation for extended periods (up to four hours at a time) typing 3 25.0 entry engineer leigh & associates- work location: remote" 1 8.333333333333332 entry engineer kunz 1 8.333333333333332 entry engineer

parts:  ['```json']
1
parts:  ['']
1
parts:  ['"Freelance Reader: Crime Fiction', ' Book of the Month', ' Fast reader, Reads 3+ books/week, Crime fiction knowledge, Communication skills, Book of the Month familiarity, 1+ year book evaluation experience",']
3
parts:  ['"Travel Vacation Specialist', ' Travel the Land Sea and Sky with Alice', ' Comprehensive training, Flexible scheduling, Travel perks, Commission-based pay",']
3
parts:  ['"Product Tester for Books and Ebooks (m/f/d)', " 's success starts with its employees. We also know that an individual's success starts with the right career opportunity. Join our team today!", ' Fast reader, Reads 3+ books/week, Crime fiction knowledge, Communication skills, Book of the Month familiarity, 1+ year book evaluation experience",']
3
parts:  ['"Data Entry Clerk', ' All Steel Service', ' Comprehensive training, Flexible scheduling, Travel perks, Commission-based pay",']
3
parts:  ['"Virtual Assistant', ' GuruNanda LLC', ' Passionate reader, E

Requirement count % adds Cluster_title 5 83.33333333333334 freelance reader: communication skills 3 50.0 freelance reader: reads 3 books/week 2 33.33333333333333 freelance reader: 1 year book evaluation experience" 2 33.33333333333333 freelance reader: crime fiction knowledge 2 33.33333333333333 freelance reader: book of the month familiarity 2 33.33333333333333 freelance reader: fast reader 2 33.33333333333333 freelance reader: comprehensive training 2 33.33333333333333 freelance reader: flexible scheduling 2 33.33333333333333 freelance reader: commission-based pay" 2 33.33333333333333 freelance reader: travel perks 2 33.33333333333333 freelance reader: passionate reader 1 16.666666666666664 freelance reader: us amazon account 1 16.666666666666664 freelance reader: english fluency 1 16.666666666666664 freelance reader: reliability" 1 16.666666666666664 freelance reader: remote work capability" 1 16.666666666666664 freelance reader:

parts:  ['"Frontend Developer', ' Mothership', ' Degree or certification in Web Development, Digital Programming, Computer Science, or equivalent experience, 3-4 years of experience, 2-3 years of experience in Digital/Web development, Strong proficiency in JavaScript, DOM manipulation, JavaScript object model, Object-Oriented concepts, design patterns, coding standards, performance improvements, Advanced knowledge of HTML5, CSS3, related technologies, Experience with TypeScript, Experience with frontend frameworks and library", "Front End Developer (contract)- Infinity Software Development, Inc- Degree or certification in Web Development, Digital Programming, Computer Science, or equivalent experience, 3-4 years of experience, 2-3 years of experience in Digital/Web development, Strong proficiency in JavaScript, DOM manipulation, JavaScript object model, Object-Oriented concepts, design patterns, coding standards, performance improvements, Advanced knowledge of HTML5, CSS3, related tech

Requirement count % adds Cluster_title experience with typescript 6 600.0 developer frontend computer science 6 600.0 developer frontend related technologies 6 600.0 developer frontend coding standards 6 600.0 developer frontend dom manipulation 6 600.0 developer frontend or equivalent experience 6 600.0 developer frontend javascript object model 6 600.0 developer frontend advanced knowledge of html5 6 600.0 developer frontend 3-4 years of experience 6 600.0 developer frontend digital programming 6 600.0 developer frontend strong proficiency in javascript 6 600.0 developer frontend 2-3 years of experience in digital/web development 6 600.0 developer frontend design patterns 6 600.0 developer frontend object-oriented concepts 6 600.0 developer frontend performance improvements 6 600.0 developer frontend css3 6 600.0 developer frontend experience with frontend frameworkslibrary" 6 600.0 developer frontend "null- null- degree or certification in web development 2 200.0 developer frontend "front end developer (contract)- infinity software development 1 100.0 developer frontend "experienced software engineer across a wide array of tech stacks- mothership- degree or certification in web development 1 100.0 developer frontend degree or certification in web development 1 100.0 developer frontend inc- degree or certification in web development 1 100.0 developer frontend "null- minware- degree or certification in web development 1 100.0 developer frontend

In [0]:
from functools import reduce
dfs = list(all_dfs_results.values())
final_df = reduce(lambda df1, df2: df1.union(df2), dfs)
final_df.display()

Requirement count % adds Cluster_title 154 99.35483870967742 data scientist python 87 56.12903225806451 data scientist sql 42 27.09677419354839 data scientist 4 years experience 29 18.70967741935484 data scientist bachelor's degree 25 16.129032258064516 data scientist pytorch 23 14.838709677419354 data scientist machine learning algorithms experience 19 12.258064516129032 data scientist 5 years python/r/matlab experience 19 12.258064516129032 data scientist machine learning techniques 19 12.258064516129032 data scientist strong algorithm development skills 19 12.258064516129032 data scientist tabular mining tools experience 19 12.258064516129032 data scientist optimization algorithms experience 19 12.258064516129032 data scientist javascript 19 12.258064516129032 data scientist big data experience" 19 12.258064516129032 data scientist free text mining" 19 12.258064516129032 data scientist 1 year data science experience 19 12.258064516129032 data scientist strong communication skills 19 12.258064516129032 data scientist mongodb" 19 12.258064516129032 data scientist strong problem-solving skills 19 12.258064516129032 data scientist healthcare mining experience 19 12.258064516129032 data scientist stock/futures prediction experience 19 12.258064516129032 data scientist tensorflow 19 12.258064516129032 data scientist 3 years data experience 18 11.612903225806452 data scientist data visualization 18 11.612903225806452 data scientist machine learning 17 10.967741935483872 data scientist 3 years experience 17 10.967741935483872 data scientist numpy 15 9.67741935483871 data scientist r 15 9.67741935483871 data scientist data mining 12 7.741935483870968 data scientist data modeling 11 7.096774193548387 data scientist etl 11 7.096774193548387 data scientist python" 11 7.096774193548387 data scientist statistical analysis 11 7.096774193548387 data scientist data cleaning 11 7.096774193548387 data scientist ai algorithms 11 7.096774193548387 data scientist gcp" 11 7.096774193548387 data scientist statistical modeling 11 7.096774193548387 data scientist opencv 10 6.451612903225806 data scientist nosql databases 10 6.451612903225806 data scientist devops 10 6.451612903225806 data scientist msc 10 6.451612903225806 data scientist machine learning algorithms 10 6.451612903225806 data scientist tableau/power bi/plotly 10 6.451612903225806 data scientist statistical methods 10 6.451612903225806 data scientist deep learning frameworks 10 6.451612903225806 data scientist mlops" 10 6.451612903225806 data scientist 5-7 years experience 10 6.451612903225806 data scientist big data tools 10 6.451612903225806 data scientist nlp/computer vision/time-series forecasting 10 6.451612903225806 data scientist pandas 9 5.806451612903226 data scientist scikit-learn 9 5.806451612903226 data scientist cloud infrastructure 9 5.806451612903226 data scientist llms 9 5.806451612903226 data scientist identity management" 9 5.806451612903226 data scientist computer vision algorithms 9 5.806451612903226 data scientist vector dbs 9 5.806451612903226 data scientist good writtenverbal skills 8 5.161290322580645 data scientist familiarity with data annotation processes 8 5.161290322580645 data scientist full-time availability 8 5.161290322580645 data scientist experience with python" 8 5.161290322580645 data scientist experience with seismic data 8 5.161290322580645 data scientist familiarity with sql 8 5.161290322580645 data scientist strong attention to detail 8 5.161290322580645 data scientist experience with matlab 8 5.161290322580645 data scientist dbt 8 5.161290322580645 data scientist bigquery 8 5.161290322580645 data scientist audio analysis 8 5.161290322580645 data scientist master's/phd 8 5.161290322580645 data scientist 6 years experience 8 5.161290322580645 data scientist nlp 8 5.161290322580645 data scientist tableau" 8 5.161290322580645 data scientist looker 8 5.161290322580645 data scientist bachelor of science degree 7 4.516129032258064 data scientist git" 